In [31]:
import os
import json
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [32]:
# ===== 用户可调整的参数 =====
root_data_dir = "C:/Users/96412/AppData/LocalLow/DefaultCompany/VRTheatre/TrailData"   # 根数据目录，里面是多个以用户名开头的子文件夹
user_name     = "Lucas"
target_video  = "20180615_monkey cinema_focal manny canada_injected_360"
time_tolerance = 0.5   # seconds


In [33]:
def normalize_horiz_angle(a: int) -> int:
    return ((a + 180) % 360) - 180

# 1. find sessions
session_dirs = []
for d in os.listdir(root_data_dir):
    if not d.startswith(user_name + "_"): continue
    parts = d.split("_", 3)
    if len(parts) == 4 and parts[3] == target_video:
        session_dirs.append(d)

# 2. compute total duration
max_dur = 0
for sess in session_dirs:
    info = json.load(open(os.path.join(root_data_dir, sess, "Horizontal.json")))
    max_dur = max(max_dur, info.get("videoDuration", 0))
total_sec = int(max_dur) + 1

# choose tick interval: every 60s if long, else every 10s
interval = 60 if total_sec > 120 else 10
tickvals = list(range(0, total_sec, interval))
if (total_sec - 1) not in tickvals:
    tickvals.append(total_sec - 1)
ticktext = [f"{val//60}:{val%60:02d}" for val in tickvals]

# 3. init accumulators
H_MIN, H_MAX = -180, 180
V_MIN, V_MAX =  -90,   90
h_cols = H_MAX - H_MIN + 1
v_cols = V_MAX - V_MIN + 1

heat_h_tot = [[0]*h_cols for _ in range(total_sec)]
heat_v_tot = [[0]*v_cols for _ in range(total_sec)]

# 4. accumulate
for sess in session_dirs:
    base = os.path.join(root_data_dir, sess)
    hj = json.load(open(os.path.join(base, "Horizontal.json")))
    vj = json.load(open(os.path.join(base, "Vertical.json")))

    pts_h = sorted(hj["points"], key=lambda x: x["time"])
    pts_v = sorted(vj["points"], key=lambda x: x["time"])
    half_h = hj.get("fov", 60) / 2.0
    half_v = vj.get("fov", 60) / 2.0

    i = j = 0
    matched = []
    while i < len(pts_h) and j < len(pts_v):
        th, tv = pts_h[i]["time"], pts_v[j]["time"]
        if abs(th - tv) <= time_tolerance:
            matched.append(((th+tv)/2, pts_h[i]["angle"], pts_v[j]["angle"]))
            i += 1; j += 1
        elif th < tv:
            i += 1
        else:
            j += 1

    for t, hc, vc in matched:
        ti = int(t)
        hc0 = int(round(hc)); vc0 = int(round(vc))

        # horizontal FOV
        for a in range(int(round(hc0-half_h)), int(round(hc0+half_h))+1):
            an = normalize_horiz_angle(a)
            ci = an - H_MIN
            heat_h_tot[ti][ci] += 1

        # vertical FOV
        for a in range(max(V_MIN, int(round(vc0-half_v))),
                       min(V_MAX, int(round(vc0+half_v)))+1):
            ci = a - V_MIN
            heat_v_tot[ti][ci] += 1

# 5. hover-text
text_h = [["" for _ in range(h_cols)] for _ in range(total_sec)]
text_v = [["" for _ in range(v_cols)] for _ in range(total_sec)]
for ti in range(total_sec):
    for ci in range(h_cols):
        cnt = heat_h_tot[ti][ci]
        if cnt:
            angle = H_MIN + ci
            text_h[ti][ci] = f"Time: {ti//60}:{ti%60:02d} | Horizontal: {angle}° | Count: {cnt}"
    for ci in range(v_cols):
        cnt = heat_v_tot[ti][ci]
        if cnt:
            angle = V_MIN + ci
            text_v[ti][ci] = f"Time: {ti//60}:{ti%60:02d} | Vertical: {angle}° | Count: {cnt}"

# 6. transpose vertical heatmap
heat_v_rot = [list(col) for col in zip(*heat_v_tot)]
text_v_rot = [list(col) for col in zip(*text_v)]

# 7. plot inverted-T
fig = make_subplots(
    rows=2, cols=3,
    specs=[[ None, {"type":"heatmap"}, None ],
           [{"colspan":3,"type":"heatmap"}, None, None]],
    column_widths=[0.1, 0.8, 0.1],
    row_heights=[0.85, 0.15],
    vertical_spacing=0.02
)

# top: horizontal-angle bar
fig.add_trace(go.Heatmap(
    z=heat_h_tot,
    x=list(range(H_MIN, H_MAX+1)),
    y=list(range(total_sec)),
    text=text_h,
    hoverinfo="text",
    colorscale="Viridis",
    zmin=0, zmax=max(1, max(map(max, heat_h_tot))),
    colorbar=dict(title="View Count", len=0.5, x=0.95, y=0.75)
), row=1, col=2)

# bottom: vertical-angle bar
fig.add_trace(go.Heatmap(
    z=heat_v_rot,
    x=list(range(total_sec)),
    y=list(range(V_MIN, V_MAX+1)),
    text=text_v_rot,
    hoverinfo="text",
    colorscale="Viridis",
    zmin=0, zmax=max(1, max(map(max, heat_v_tot))),
    showscale=False
), row=2, col=1)

# axis settings
fig.update_xaxes(title_text="Horizontal Angle (°)", range=[H_MIN, H_MAX], row=1, col=2)
fig.update_yaxes(
    title_text="Time (mm:ss)",
    autorange=False,
    range=[0, total_sec-1],
    tickmode="array",
    tickvals=tickvals,
    ticktext=ticktext,
    showticklabels=True,
    row=1, col=2
)

fig.update_xaxes(
    title_text="Time (mm:ss)",
    range=[0, total_sec-1],
    tickmode="array",
    tickvals=tickvals,
    ticktext=ticktext,
    row=2, col=1
)
fig.update_yaxes(title_text="Vertical Angle (°)", range=[V_MIN, V_MAX], row=2, col=1)

# layout
fig.update_layout(
    title_text=f"{user_name} — {target_video} Combined Heatmap",
    height=1000,
    width=1200,
    margin=dict(t=40, b=20)
)

fig.show()